In [8]:
'''#Things needed to download the video
!pip install --upgrade pytubefix
!pip show pytube

# Library for audio to text
!pip install openai-whisper

# Library for scenedetection
!pip install scenedetect
!pip install pytubefix

# Library for extracting the metadata
!pip install tinytag

#Library for Subtitle
!pip install youtube-transcript-api

#Library for the checking the text
!pip install sentence-transformers scikit-learn transformers pandas nltk'''

'#Things needed to download the video\n!pip install --upgrade pytubefix\n!pip show pytube\n\n# Library for audio to text\n!pip install openai-whisper\n\n# Library for scenedetection\n!pip install scenedetect\n!pip install pytubefix\n\n# Library for extracting the metadata\n!pip install tinytag\n\n#Library for Subtitle\n!pip install youtube-transcript-api\n\n#Library for the checking the text\n!pip install sentence-transformers scikit-learn transformers pandas nltk'

In [9]:
import gradio as gr

In [40]:
# Library to import for the video download
from pytubefix import YouTube
from pytubefix.cli import on_progress

# Library to import for the ContentDetection
from scenedetect import VideoManager, SceneManager
from scenedetect.detectors import ContentDetector
from moviepy import VideoFileClip

# Library for extracting the metadata
from tinytag import TinyTag

# Library for extracting audio
import moviepy as mp

#Library for concating the video
from moviepy import VideoFileClip, concatenate_videoclips
from scenedetect import FrameTimecode

# Library for the subtitile
from youtube_transcript_api import YouTubeTranscriptApi
from urllib.parse import urlparse, parse_qs
import whisper
from pydub import AudioSegment

#Library needed for the scenedetection
import scenedetect
from scenedetect import open_video
from scenedetect import detect, ContentDetector, split_video_ffmpeg

# Library for the checking the summarization and similarity
from sentence_transformers import SentenceTransformer, util
import torch
from sklearn.metrics.pairwise import cosine_similarity
from transformers import pipeline
import nltk
from nltk.tokenize import sent_tokenize

import pandas as pd
from IPython.display import Video, display
from datetime import datetime
from typing import Dict, List
import os

In [11]:
# Calling the models
summarizer= pipeline("summarization")
nltk.download('punkt_tab')
nltk.download('punkt')

#Load a pre-trained sentence embedding model
model = SentenceTransformer('all-MiniLM-L6-v2')

No model was supplied, defaulted to sshleifer/distilbart-cnn-12-6 and revision a4f8f3e (https://huggingface.co/sshleifer/distilbart-cnn-12-6).
Using a pipeline without specifying a model name and revision in production is not recommended.
[nltk_data] Downloading package punkt_tab to
[nltk_data]     C:\Users\Anith\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\Anith\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [12]:
def download_youtube_video(filename="Sample.mp4"):
    """
    provide the Url
    """
    try:
        #Asking for the url
        url=str(input("Enter the url of the video"))

        # Create a YouTube object
        yt = YouTube(url)

        # Get the Video
        stream = yt.streams.filter(file_extension="mp4", progressive=True).first()

        # Download the video with a specific filename (if provided)
        if filename:
            downloaded_file = stream.download(filename=filename)
        else:
            downloaded_file = stream.download()

        # Print the name of the downloaded file
        print(f"Video downloaded successfully: {downloaded_file}")

    except Exception as e:
        print(f"An error occurred: {e}")

    return url, downloaded_file

In [13]:
def extract_video_id(url:str):
  """ RUN INSIDE"""
  parsed=urlparse(url)
  if parsed.hostname in {"www.youtube.com","youtube.com"}:
    qs=parse_qs(parsed.query)
    if "v" in qs:
      return qs["v"][0]
  return parsed.path.lstrip("/")

In [14]:
def extract_sub(url:str):
  """
  url : Enter the url of the video you need to extract


  Enter the Url and the function will try to get the
  subtitle of the video and the timestamp of the subtitle,
  Create a dataframe out of it"""

  video_id=extract_video_id(url)
  ytt_api=YouTubeTranscriptApi()
  subtitle=ytt_api.fetch(video_id)
  data =[{"text": s.text, "start": s.start, "duration": s.duration} for s in subtitle.snippets]
  dataframe=pd.DataFrame(data)
  return dataframe

In [15]:
def download_subtitle_or_transcribe(url,download_path):
  """ Try to download the subtitle else audio Transcription

  URL : Pass the Url

  Download_path : Pass the download path of the video
  """
  try:
    video_id=extract_video_id(url)
    ytt_api=YouTubeTranscriptApi()
    subtitle=ytt_api.fetch(video_id)
    data =[{"text": s.text, "start": s.start, "duration": s.duration, "end": s.start + s.duration } for s in subtitle.snippets]
    dataframe=pd.DataFrame(data)
    return dataframe
  except Exception as e:
    video_audio = AudioSegment.from_file(download_path)
    video_audio.export("audio.wav", format="wav")
    model = whisper.load_model("base")
    result = model.transcribe("audio.wav", language="en", verbose=False)
    segments = result["segments"]
    df = pd.DataFrame(segments)
    selected_df = df[['start', 'end', 'text']]
    return selected_df

In [16]:
def table_to_paragraph(data):
  """
  Changing the DataFrame into paragragh

  data: Pass the Data Table contain the start, end , text

  """
  text_list=data['text']
  for i in text_list:
    paragraph=" ".join(data["text"])
  return paragraph

In [17]:
def chunk_text(text, max_chunk_length=1000):
    """ RUN INSIDE"""
    # Split text into chunks of max_chunk_length characters
    return [text[i:i+max_chunk_length] for i in range(0, len(text), max_chunk_length)]

In [18]:
def summarize(text, max_length=80, min_length=50):
    """
    Text : The Long text of paragraph of data

    max_lenght : Max lenght of the summarized text

    min_lenght : MIn lenght of the summarized text

    Changing the long text into the important point to know
    """
    chunks = chunk_text(text)
    summaries = []

    for chunk in chunks:
        result = summarizer(chunk, max_length=max_length, min_length=min_length, do_sample=False)
        if result and isinstance(result, list):
            summaries.append(result[0]['summary_text'])

    return " ".join(summaries)

In [19]:
def encode(text, table):
  """
  text : The summarized sentence

  table : Pass the Data Table contain the start, end , text

  """
  key_embeddings = model.encode(text, convert_to_tensor=True)
  data_embeddings=model.encode(table['text'].tolist(), convert_to_tensor=True)
  key_index=[]
  for key_emb in key_embeddings:
    similarities=util.cos_sim(key_emb, data_embeddings)[0]
    best_match= torch.argmax(similarities).item()
    key_index.append(best_match)
  return key_index

In [34]:
def scene_detected(path:str)-> str:
  """
  path : The Path of the download video

  Help to detected the scene in the video
  """
  scenes=detect(path, ContentDetector())
  data=[]
  for (scene_start, scene_end) in scenes:
    data.append({"Scene_start":scene_start, "Scene_end":scene_end})
  show_data=pd.DataFrame(data)
  return data, show_data

In [21]:
def keyword_for_unboxing(data):
  """
  data : Pass the Data Table contain the start, end , text

  finding the presence of the keywords in the video for unboxing n'll.
  """
  key_index=[]
  keywords=["unbox", "box", "open the box", "take out", "out of the box",
            "final", "verdict", "recommend", "don't buy", "buy", "overall",
            "conclusion", "impression","price",  "Unboxing experience","First impressions",
            "What’s in the box","Fresh out of the box","Sealed package","Brand new device",
            "Hands-on review","Initial setup","Quick look","Tech unboxing",]
  keywords_lower=[kw.lower() for kw in keywords]
  for index, sentence in data['text'].items():
    if any(kw in sentence.lower() for kw in keywords_lower):
      key_index.append(index)
  return key_index


In [22]:
def key_fact_of_video(paragraph):
  """
  paragraph : summarized paragraph having the key facts

  sort of find the right things for the short clip video
  Most of time half of the paragraph is relevant
  """
  sentence=[s.strip() for s in paragraph.split(".") if s.strip()]

  core_keywords=tech_keywords = [
    # Display
    "display", "screen", "panel", "display quality", "display resolution", "brightness", "nits",
    "contrast ratio", "color accuracy", "HDR", "HDR10", "Dolby Vision", "refresh rate", "adaptive refresh rate",
    "variable refresh rate", "hz", "OLED", "AMOLED", "Super AMOLED", "Retina display", "LTPO", "LCD",
    "mini-LED", "micro-LED", "touchscreen", "edge-to-edge display", "bezel", "always-on display",
    "gorilla glass", "anti-glare", "display protection",

    # Camera
    "camera", "megapixel", "rear camera", "front camera", "selfie", "ultrawide", "telephoto", "macro",
    "depth sensor", "aperture", "OIS", "EIS", "stabilization", "AI camera", "portrait mode", "night mode",
    "HDR photo", "zoom", "optical zoom", "digital zoom", "camera test", "video recording", "slow motion",
    "4K video", "8K video", "capture",

    # Battery & Charging
    "battery", "battery life", "battery backup", "fast charging", "wireless charging", "reverse charging",
    "charging speed", "USB-C charging", "power adapter", "wattage", "battery test", "endurance", "charger",
    "battery health",

    # Performance
    "processor", "chip", "chipset", "GPU", "CPU", "AI engine", "NPU", "performance", "benchmark",
    "gaming benchmark", "fps", "cooling system", "thermal management", "multitasking", "RAM", "ROM",
    "storage", "SSD", "HDD", "expandable storage", "performance test", "app load time", "boot-up speed",
    "heat dissipation",

    # Design & Build
    "design", "build quality", "build and design", "weight", "thickness", "material", "finish",
    "aesthetics", "color options", "ergonomics", "durability", "water resistance", "dust resistance",
    "IP rating", "2-in-1 convertible", "hinge", "keyboard feel", "trackpad response", "port selection",

    # Audio
    "speaker", "stereo speakers", "Dolby Atmos", "Hi-Res audio", "sound quality", "bass", "treble",
    "volume", "microphone", "audio jack", "bluetooth audio", "codec", "media playback",

    # Connectivity
    "USB", "USB-C", "Thunderbolt", "Wi-Fi", "Wi-Fi 6", "Wi-Fi 7", "Bluetooth", "Bluetooth 5.3",
    "NFC", "GPS", "cellular", "5G", "4G", "dual SIM", "eSIM", "port selection",

    # Security
    "fingerprint sensor", "face unlock", "security", "privacy", "biometrics", "encryption", "screen lock",

    # Software
    "Android", "iOS", "UI", "user interface", "software update", "custom skin", "OS version", "bloatware",
    "app performance", "productivity test", "multimedia experience", "Android setup", "iOS setup",

    # Price & Verdict
    "deal", "price", "offer", "value for money", "recommend", "final verdict", "conclusion",
    "overall impression", "buy", "don't buy", "compare", "comparison", "flagship phone", "midrange",
    "budget", "premium"
    ]

  core_keyword_sentence=[
    s for s in sentence
    if any(kw.lower() in s.lower() for kw in core_keywords)]

  return core_keyword_sentence



In [23]:
def overlapping(select_row,list):
  """
  select_row : The selected row table contain the start and end

  list : The index of the key fact sentence

  """
  data=select_row.sort_values(by="start").reset_index(drop=True)
  non_overlapping=[]
  last_end= -float("inf")

  for _, row in data.iterrows():
    if row['start'] >= last_end:
      non_overlapping.append(row)
      last_end= row["end"]

  return pd.DataFrame(non_overlapping)

In [25]:
"""def time_to_seconds(t):
    dt = datetime.strptime(t, "%H:%M:%S.%f")
    return dt.hour * 3600 + dt.minute * 60 + dt.second + dt.microsecond / 1e6"""


'def time_to_seconds(t):\n    dt = datetime.strptime(t, "%H:%M:%S.%f")\n    return dt.hour * 3600 + dt.minute * 60 + dt.second + dt.microsecond / 1e6'

In [26]:
def time_to_seconds(time_str):
    """
    Converts HH:MM:SS or HH:MM:SS.mmm to total seconds safely.
    """
    import re

    # Extract numbers
    parts = re.split('[:.]', time_str)
    parts = [float(p) for p in parts if p.strip() != '']

    # Handle missing parts (like MM:SS)
    while len(parts) < 3:
        parts.insert(0, 0.0)

    h, m, s = parts[:3]

    # Fix invalid values
    if s >= 60:
        s = 59.999
    if m >= 60:
        m = 59

    return h * 3600 + m * 60 + s


In [27]:
def select_row(data, clip_list):
  """
  data : Pass the Data Table contain the start, end , text

  clip_list : The list of index that have the important content
  """
  cols=["start","end"]
  result = [x - 1 for x in clip_list]
  selected_rows=data.iloc[result][cols]
  return selected_rows

In [28]:
def matchingScene(selected_rows,scene_data):
  """
  selected_rows : The index and the start/end time of video imp

  scene_data : The detect scene from the video
  """
  scene_start_seconds=[time_to_seconds(str(scene["Scene_start"])) for scene in scene_data]
  matching_indices=[]
  for start_time in selected_rows['start']:
    closed_index=min(range(len(scene_start_seconds)), key=lambda i: abs(scene_start_seconds[i] - start_time))
    matching_indices.append(closed_index)
  return matching_indices

In [29]:
from typing import Dict, List
def merge_video(data=List[Dict],path=str,clip=list):
  """
  data: The List of start and end point of scenedetection

  path: Path of the video

  clip[List]: The list of scene need to be merge

  """

  clip_path=VideoFileClip(path)
  split_clips=[]

  for arg in clip:
    scene=data[arg]
    start_tc=scene["Scene_start"]
    end_tc=scene["Scene_end"]

    start_sec=start_tc.get_seconds()
    end_sec=end_tc.get_seconds()

    split_clips.append(clip_path.subclipped(start_sec, end_sec))

  final_clip=concatenate_videoclips(split_clips)
  output_path = os.path.abspath("merge.mp4")
  final_clip.write_videofile(output_path)

  return output_path


In [30]:
def display_video(video_path="/content/merge.mp4"):
  """
  video_path : The Path of the video
  """
  print("▶️ Playing video...")
  display(Video(video_path, embed=True, width=640, height=360))

In [ ]:
 '''key_index.append(data.index[data['text'].apply(
      lambda sentence: any(kw in sentence.lower() for kw in keywords_lower))])'''

"key_index.append(data.index[data['text'].apply(\n     lambda sentence: any(kw in sentence.lower() for kw in keywords_lower))])"

## ______________________________________________________________________________

In [ ]:
url, download_path= download_youtube_video()

Video downloaded successfully: d:\DATA SCIENCE\ICTAK\INTERNSHIP\Sample.mp4


In [ ]:
data=download_subtitle_or_transcribe(url, download_path)

In [ ]:
data

text    start  duration  \
0                - The best thing about the iPhone Air    0.600     2.790   
1    is actually how much it\nseems to have freed A...    3.390     2.850   
2                to make the Pro phones even more pro.    6.240     3.123   
3                         (slow dramatic techno music)   10.432     3.750   
4               (slow dramatic techno music continues)   22.936     4.583   
..                                                 ...      ...       ...   
301                               Thanks for watching.  730.590     1.320   
302    Catch you guys very soon,\nstill in Techtember,  731.910     3.000   
303                                   in the next one.  734.910     1.470   
304                                             Peace.  736.380     1.200   
305                        (light upbeat techno music)  737.580     3.667   

         end  
0      3.390  
1      6.240  
2      9.363  
3     14.182  
4     27.519  
..       ...  
301  731.910  
302  734.910  
303  736.380  
304  737.580  
305  741.247  

[306 rows x 4 columns]

In [ ]:
keyword=keyword_for_unboxing(data)
print(keyword)

[92, 217, 287, 288]


In [ ]:
paragraph = table_to_paragraph(data)
print(paragraph)

- The best thing about the iPhone Air is actually how much it
seems to have freed Apple up to make the Pro phones even more pro. (slow dramatic techno music) (slow dramatic techno music continues) (slow dramatic techno music fading) Have you noticed that? These new Pro phones are
thicker than last year, more room inside for bigger batteries, and a vapor chamber, and a bigger camera. It's not quite on the
level of the Ultra phones, but this is the most maximalist that an iPhone has ever
felt, and I like it. But also, let me let you in on a little not-so-secret secret. The Pro phone is always
the best selling one. Like this year, the iPhone
Air is the most interesting and it's getting the most YouTube
clicks and the most views, but then the Base 17 is
more than ever the one that most people should
get and the best deal. But it turns out the
Pro Max, specifically, by far, is the most
popular, by sales numbers. I was gonna try to find a
way to show you guys this, you know, channel sponsor 

In [ ]:
summary = summarize(paragraph)
print(summary)

 The Pro phone is always the best selling one, but the Base 17 is the best deal . The Pro Max phone is the most popular phone, by sales numbers . The iPhone Air is most interesting and it's getting the most YouTube views and the most views, but also the most expensive .  Dbrand, which makes an accessory for every model of iPhone, sells 90% of orders this year . Over half our Pro Maxes, we're seeing Apple walk this line between being a more pro-phone than ever before and this maximalist new design and everything they're doing, but also, being literally the most mainstream phone of all-time .  The new camera has three matching 48-megapixel cameras, all of which are super reliable, just as good for casualshooters as they are for people who depend on their iPhone for work . All of your zoom shots will have much more detail and less noise, thanks to the sensor being much larger and much higher resolution .  ProRes raw footage from the iPhone 17 Pro can go into the new Final Cut Pro 11.2, I 

In [ ]:
text=key_fact_of_video(summary)

In [ ]:
text

['The Pro phone is always the best selling one, but the Base 17 is the best deal',
 "Over half our Pro Maxes, we're seeing Apple walk this line between being a more pro-phone than ever before and this maximalist new design and everything they're doing, but also, being literally the most mainstream phone of all-time",
 'The new camera has three matching 48-megapixel cameras, all of which are super reliable, just as good for casualshooters as they are for people who depend on their iPhone for work',
 'All of your zoom shots will have much more detail and less noise, thanks to the sensor being much larger and much higher resolution',
 'ProRes raw footage from the iPhone 17 Pro can go into the new Final Cut Pro 11',
 "It's not a huge difference from last year, but it's nice, but the file sizes aversus last year",
 "It's not often that the newest phones actually change a lot and get thicker and heavier, but like I said, I think that's kind of one of my favorite things about the new design",

In [ ]:
list2=encode(text, data)
list2

[15,
 32,
 66,
 52,
 89,
 88,
 118,
 132,
 135,
 187,
 137,
 194,
 198,
 200,
 230,
 213,
 259,
 288,
 287]

In [ ]:
list2.extend(keyword)
list2

[15,
 32,
 66,
 52,
 89,
 88,
 118,
 132,
 135,
 187,
 137,
 194,
 198,
 200,
 230,
 213,
 259,
 288,
 287,
 92,
 217,
 287,
 288]

In [ ]:
scene_detect, show_data = scene_detected(download_path)

In [ ]:
print(scene_detect)
print(" ")
print(show_data)

[{'Scene_start': 00:00:00.000 [frame=0, fps=29.970], 'Scene_end': 00:00:13.680 [frame=410, fps=29.970]}, {'Scene_start': 00:00:13.680 [frame=410, fps=29.970], 'Scene_end': 00:00:14.281 [frame=428, fps=29.970]}, {'Scene_start': 00:00:14.281 [frame=428, fps=29.970], 'Scene_end': 00:00:18.585 [frame=557, fps=29.970]}, {'Scene_start': 00:00:18.585 [frame=557, fps=29.970], 'Scene_end': 00:00:27.427 [frame=822, fps=29.970]}, {'Scene_start': 00:00:27.427 [frame=822, fps=29.970], 'Scene_end': 00:00:42.309 [frame=1268, fps=29.970]}, {'Scene_start': 00:00:42.309 [frame=1268, fps=29.970], 'Scene_end': 00:00:57.591 [frame=1726, fps=29.970]}, {'Scene_start': 00:00:57.591 [frame=1726, fps=29.970], 'Scene_end': 00:01:05.032 [frame=1949, fps=29.970]}, {'Scene_start': 00:01:05.032 [frame=1949, fps=29.970], 'Scene_end': 00:01:07.968 [frame=2037, fps=29.970]}, {'Scene_start': 00:01:07.968 [frame=2037, fps=29.970], 'Scene_end': 00:01:10.837 [frame=2123, fps=29.970]}, {'Scene_start': 00:01:10.837 [frame=21

In [ ]:
selected_rows=select_row(data, list2)
print(selected_rows)

      start     end
14    59.16   61.62
31   109.80  113.10
65   190.80  193.29
51   155.28  157.32
88   240.87  244.29
87   239.04  240.87
117  305.43  307.38
131  335.82  338.31
134  344.55  346.59
186  463.35  466.32
136  348.93  349.95
193  482.94  485.10
197  492.36  495.03
199  496.98  498.42
229  571.77  573.12
212  528.96  532.47
258  636.75  638.79
287  703.56  705.30
286  702.15  703.56
91   250.68  252.12
216  539.49  541.56
286  702.15  703.56
287  703.56  705.30


In [ ]:
non_overlap=overlapping(selected_rows, list2)
non_overlap

start     end
0    59.16   61.62
1   109.80  113.10
2   155.28  157.32
3   190.80  193.29
4   239.04  240.87
5   240.87  244.29
6   250.68  252.12
7   305.43  307.38
8   335.82  338.31
9   344.55  346.59
10  348.93  349.95
11  463.35  466.32
12  482.94  485.10
13  492.36  495.03
14  496.98  498.42
15  528.96  532.47
16  539.49  541.56
17  571.77  573.12
18  636.75  638.79
19  702.15  703.56
21  703.56  705.30

In [ ]:
matching_index = matchingScene(non_overlap, scene_detect)

In [ ]:
matching_index

[6,
 12,
 24,
 31,
 35,
 35,
 36,
 43,
 49,
 50,
 51,
 65,
 68,
 69,
 70,
 72,
 74,
 79,
 85,
 90,
 91]

In [ ]:
#merge_video(scene_detect, download_path, matching_index)

In [ ]:
matching_index

[20, 22, 25, 27, 28, 40, 57, 60, 68]

In [ ]:
clip_path=VideoFileClip(download_path)
split_clips=[]
clip_path


In [ ]:
for arg in matching_index:
    scene=scene_detect[arg]
    start_tc=scene["Scene_start"]
    end_tc=scene["Scene_end"]

    start_sec=start_tc.get_seconds()
    end_sec=end_tc.get_seconds()

    split_clips.append(clip_path.subclipped(start_sec, end_sec))

In [ ]:
final_clip=concatenate_videoclips(split_clips)

In [ ]:
final_clip.write_videofile("merge.mp4")

MoviePy - Building video merge.mp4.
MoviePy - Writing audio in mergeTEMP_MPY_wvf_snd.mp3


MoviePy - Done.
MoviePy - Writing video merge.mp4



MoviePy - Done !
MoviePy - video ready merge.mp4


In [ ]:
merge_video(scene_detect, download_path, matching_index)

MoviePy - Building video merge.mp4.
MoviePy - Writing audio in mergeTEMP_MPY_wvf_snd.mp3


MoviePy - Done.
MoviePy - Writing video merge.mp4



MoviePy - Done !
MoviePy - video ready merge.mp4


In [ ]:
display_video(video_path="D:\DATA SCIENCE\ICTAK\INTERNSHIP\merge.mp4")

▶️ Playing video...


## I Final Try with Hyper tuning done

In [31]:
import time

In [46]:
def run_to_here1() -> str:
    try:
        start_time=time.time()
        print("Step 1: Downloading YouTube video...")
        url, download_path = download_youtube_video()
        print("✅ Done: Video downloaded\n")

        print("Step 2: Getting subtitles or transcribing...")
        data = download_subtitle_or_transcribe(url=url, download_path=download_path)
        print("✅ Done: Subtitle/Transcript ready\n")

        print("Step 3: Converting transcript table to paragraph...")
        paragraph = table_to_paragraph(data)
        print("✅ Done: Paragraph generated\n")

        print("Step 4: Summarizing paragraph...")
        summary = summarize(paragraph)
        print("✅ Done: Summary complete\n")

        print("Step 5 : Finding the unboxing part")
        unboxing=keyword_for_unboxing(data)
        print(f"✅ Done: Unboxing \n ")

        print("Step 6 : Finding the key facts")
        text=key_fact_of_video(summary)
        print("✅ Done: found the facts")

        print("Step 7: Encoding summary into clip list...")
        clip_list = encode(text, data)
        clip_list=clip_list+unboxing
        print(f"✅ Done: Clip list encoded\n {clip_list}")

        print("Step 8: Detecting scenes...")
        scene_detect, show_data = scene_detected(download_path)
        print("✅ Done: Scenes detected\n")

        print("Step 9: Selecting relevant rows...")
        select_rows = select_row(data, clip_list)
        print("✅ Done: Rows selected\n")

        print("step 10 : Find is there any overlapping")
        non_overlapping=overlapping(select_rows, clip_list)
        print("✅ Done: nonoverlapping-Rows selected\n")

        print("Step 11: Matching selected rows to detected scenes...")
        matching_index = matchingScene(non_overlapping, scene_detect)
        print("✅ Done: Matching complete\n")

        print("Step 12: Merging video clips...")
        output_path=merge_video(scene_detect, download_path, matching_index)
        print("✅ Done: Final video merged successfully\n")

        print("Watch it ")
        display_video(output_path)
        print("✅  Thank you for watching")


        end_time=time.time()
        runtime=end_time - start_time

        return f"🎉 All steps completed successfully!\n {runtime}"

    except Exception as e:
        print(f"❌ Error during pipeline: {e}")
        raise




In [47]:
run_to_here1()

Step 1: Downloading YouTube video...
Video downloaded successfully: d:\DATA SCIENCE\ICTAK\INTERNSHIP\Sample.mp4
✅ Done: Video downloaded

Step 2: Getting subtitles or transcribing...


100%|███████████████████████████████████████| 139M/139M [00:37<00:00, 3.88MiB/s]
d:\SOFTWARE\CODE\Anaconda\envs\internship\Lib\site-packages\whisper\transcribe.py:115: UserWarning: FP16 is not supported on CPU; using FP32 instead
  warnings.warn("FP16 is not supported on CPU; using FP32 instead")
100%|██████████| 19704/19704 [00:19<00:00, 996.62frames/s] 


✅ Done: Subtitle/Transcript ready

Step 3: Converting transcript table to paragraph...
✅ Done: Paragraph generated

Step 4: Summarizing paragraph...
✅ Done: Summary complete

Step 5 : Finding the unboxing part
✅ Done: Unboxing 
 
Step 6 : Finding the key facts
✅ Done: found the facts
Step 7: Encoding summary into clip list...
✅ Done: Clip list encoded
 []
Step 8: Detecting scenes...
✅ Done: Scenes detected

Step 9: Selecting relevant rows...
✅ Done: Rows selected

step 10 : Find is there any overlapping
✅ Done: nonoverlapping-Rows selected

Step 11: Matching selected rows to detected scenes...
❌ Error during pipeline: 'start'


KeyError: 'start'